### Overview
Code to understand RNN via implementation based in numpy. Minimal character-level Vanilla RNN model. 
Backprop also implemented in numpy as part of the project. 

Based on notebook by Andrej Karpathy (@karpathy)

Modified by : Falak Shah & Twisha Naik

In [1]:
# No other dependencies!! 
import numpy as np

In [2]:
# data I/O
data = open('min_char_rnn_input.txt', 'r').read() # should be simple plain text file
chars = list(set(data)) # Get set of unique characters
data_size, vocab_size = len(data), len(chars)
print("Total char in data: " + str(data_size))
print("Unique char in data: " + str(vocab_size))

Total char in data: 1115394
Unique char in data: 65


In [3]:
# Mapping dictionaries from character to integer and back
char_to_ix = { ch:i for i,ch in enumerate(chars) }
ix_to_char = { i:ch for i,ch in enumerate(chars) }

In [5]:
# char_to_ix

In [6]:
chars.sort()
print(chars)

['\n', ' ', '!', '$', '&', "'", ',', '-', '.', '3', ':', ';', '?', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']


In [ ]:
# hyperparameters
hidden_size = 100 # size of hidden layer of neurons
seq_length = 25 # number of steps to unroll the RNN for
learning_rate = 1e-1

In [3]:
# model parameters
Wxh = np.random.randn(hidden_size, vocab_size)*0.01 # input to hidden
Whh = np.random.randn(hidden_size, hidden_size)*0.01 # hidden to hidden
Why = np.random.randn(vocab_size, hidden_size)*0.01 # hidden to output
bh = np.zeros((hidden_size, 1)) # hidden bias
by = np.zeros((vocab_size, 1)) # output bias

\begin{equation}
\label{eq:ht}
    h_t = tanh(W_{hh}h_{t-1} + W_{xh}x_t)
\end{equation}
\begin{equation}
    y_t = W_{hy}h_t
    \label{eq:yt}
\end{equation}

In [7]:
def lossandgrads(inputs, targets, hprev):
  """
  inputs,targets are both list of integers.
  hprev is Hx1 array of initial hidden state
  returns the loss, gradients on model parameters, and last hidden state
  """
  xs, hs, ys, ps = {}, {}, {}, {}
  hs[-1] = np.copy(hprev)
  loss = 0
  
  # forward pass
  for t in range(len(inputs)):
    xs[t] = np.zeros((vocab_size,1)) # encode in 1-of-k representation
    xs[t][inputs[t]] = 1
    hs[t] = np.tanh(np.dot(Wxh, xs[t]) + np.dot(Whh, hs[t-1]) + bh) # hidden state
    ys[t] = np.dot(Why, hs[t]) + by # unnormalized log probabilities for next chars
    ps[t] = np.exp(ys[t]) / np.sum(np.exp(ys[t])) # probabilities for next chars
    loss += -np.log(ps[t][targets[t],0]) # softmax (cross-entropy loss)
  
  # backward pass: compute gradients going backwards
  dWxh, dWhh, dWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)
  dbh, dby = np.zeros_like(bh), np.zeros_like(by)
  dhnext = np.zeros_like(hs[0])
  for t in reversed(range(len(inputs))):
    dy = np.copy(ps[t])
    dy[targets[t]] -= 1 
    dWhy += np.dot(dy, hs[t].T)
    dby += dy
    dh = np.dot(Why.T, dy) + dhnext # backprop into h
    dhraw = (1 - hs[t] * hs[t]) * dh # backprop through tanh nonlinearity
    dbh += dhraw
    dWxh += np.dot(dhraw, xs[t].T)
    dWhh += np.dot(dhraw, hs[t-1].T)
    dhnext = np.dot(Whh.T, dhraw)
  
  for dparam in [dWxh, dWhh, dWhy, dbh, dby]:
    np.clip(dparam, -5, 5, out=dparam) # clip to mitigate exploding gradients
  return loss, dWxh, dWhh, dWhy, dbh, dby, hs[len(inputs)-1]

In [8]:
def sample(h, seed_ix, n):
  """ 
  Sample output based on predicted probabilities of all characters in the vocabulary. RNN model used to predict 
  output probabilities. 
  h is memory state
  seed_ix is index for the seed letter for first time step
  n is the length of character sequence we wish to generate
  
  Returns: n length generated character sequence
  """
  x = np.zeros((vocab_size, 1))
  x[seed_ix] = 1
  ixes = []
  for t in range(n):
    h = np.tanh(np.dot(Wxh, x) + np.dot(Whh, h) + bh)
    y = np.dot(Why, h) + by
    p = np.exp(y) / np.sum(np.exp(y))
    ix = np.random.choice(range(vocab_size), p=p.ravel())
    x = np.zeros((vocab_size, 1))
    x[ix] = 1
    ixes.append(ix)
  return ixes

In [6]:
n, p = 0, 0
mWxh, mWhh, mWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)
mbh, mby = np.zeros_like(bh), np.zeros_like(by) # memory variables for Adagrad
smooth_loss = -np.log(1.0/vocab_size)*seq_length # loss at iteration 0

In [7]:
while True:
  # prepare inputs (we're sweeping from left to right in steps seq_length long)
  if p+seq_length+1 >= len(data) or n == 0: 
    hprev = np.zeros((hidden_size,1)) # reset RNN memory
    p = 0 # go from start of data
  inputs = [char_to_ix[ch] for ch in data[p:p+seq_length]]
  targets = [char_to_ix[ch] for ch in data[p+1:p+seq_length+1]]

  # sample from the model now and then
  if n % 100 == 0:
    sample_ix = sample(hprev, inputs[0], 200)
    txt = ''.join(ix_to_char[ix] for ix in sample_ix)

  # forward seq_length characters through the net and fetch gradient
  loss, dWxh, dWhh, dWhy, dbh, dby, hprev = lossandgrads(inputs, targets, hprev)
  smooth_loss = smooth_loss * 0.999 + loss * 0.001
  if n % 1000 == 0: 
        print('----\n %s \n----' % (txt, ))
        print ('iter %d, loss: %f' % (n, smooth_loss)) # print progress
  
  # perform parameter update with Adagrad
  for param, dparam, mem in zip([Wxh, Whh, Why, bh, by], 
                                [dWxh, dWhh, dWhy, dbh, dby], 
                                [mWxh, mWhh, mWhy, mbh, mby]):
    mem += dparam * dparam
    param += -learning_rate * dparam / np.sqrt(mem + 1e-8) # adagrad update

  p += seq_length # move data pointer
  n += 1 # iteration counter 

----
 -V,&MEFXQEHvzPw$'LXNOoj&wolO
qNczTwV.:jxZM&Ds,kbuJC.Y.X$d?shR&UsaSTjrkvjHuDgLFanKm.M-,K. SprlKgeZ!s;TMs fVucSahPNZzukblD
zaNENXQmi?m&.,I.Ki,hq:ecl .LdCo'bxN?XDu:,-&PhXMlLBkBz?Ir!ZS:jbxYMkl cq3?NzsRcko 
----
iter 0, loss: 104.359684
----
 Yiueas,biayily vhowd wisghhi
nh s! ts relworos t t iwsnH
n-tep we
mabe lap ctaf
uratibo outeanse h hos   asanrhiprume S s htdy nrqie noh yhle mo yo an tithe
lthwe;d w n at

?LPlitabanire gkr
n
Thedhit 
----
iter 1000, loss: 89.371389
----
 lledrmere se mow ne ttoet yaps helCrar e. noThdtso hangent the deosthas toni
Rhe rove bikirt at;
Bf to wene.

chaco if.
Te weder is ti ge wes acth ef hamenbluf homeanded wyod pof my ucar whanls Avount 
----
iter 2000, loss: 75.516509
----
  van mon wnRmgorit towd,,n senghire inpus
He Rbvois hat.
Tof wthit ket acanoth I:
ro wucat,

CFUCORIMLRIUSO fouddd,

NORGLRANSnranf, the thie s, leshasit.
Teny?s,t. he eogi
Su w meot sabersr yow lacir 
----
iter 3000, loss: 67.518988
----
 st ion The als aret toen
Th reouan



----
 soul, goas, y's: ane love lon ann you, ie youd ed lele thise, sore? shead ap my Wach fronh derester, you myaan' -Ifureset.

WOPGL:: in: Carming nis
Pirtimeser simu?

PLOUS:
Clit and yor toot of de too 
----
iter 35000, loss: 55.459964
----
 old thimh quak ef asws of ma tmastefe tiut as bercott?

FULIS:
Nou yof ind thad sowist derletiKe it oef,, med, mrPued:
Pelt.

BISAUS:
I yhous:
Thouint fathen toul,
Ifver,;
Sare,
Coos at buter.
Ard.

E 
----
iter 36000, loss: 54.672465
----
 t if and now as agamme.

Eot Warmin?
Or a you cakle thou gon? I our famh at a had gereson,
HE hat dardrare:
O me how ouof,
-for hav on me! Pyo start yo,

IfTO:
Nowd bontle lend
Mayk
Tfo wer rever wset 
----
iter 37000, loss: 55.121014
----
 l tot'd weinder,
Dand ly Velm, afweanfur hey sous of ar oo gearet ieverrer domitr his Waven?
I sust;
The fsecend trleins powle be tou
se ble astoye Hanty hit in thad t vize? hor silt sing siths foy ve 
----
iter 38000, loss: 54.419449
----
 n whis duttitind wolchin' ef h

----
 ss o, entend youeti; comefink yid ard my thes art, furer toy' illst thoud forss,
As hire LO by vire theen in necee.

IED:
Reamet,
Balles wit thou, deard.
Forst,
Tus harrtied vending tre, IN
Ard ut thy 
----
iter 69000, loss: 53.298644
----
 me Lowgryep gurod hered,
And keing geco, I
Yor fathy:
Daffia, Roll he receler, no hi bene Mowntes.
Und!

BAR:
OF witt my wadd;
I's
The my thoungring dowloen deer bom thow my you breenvet myteed?

RETA 
----
iter 70000, loss: 52.719499
----
 'erfin Ind!
Thew of I the bes a gaprond mothe are hist, up trice
To fell aes
Rotor cang her mos J yom andel his holy you Is of Henoor of there whondeh his leve,
The lide?
'll,,
Afard fooss.
Bes;
Ke be 
----
iter 71000, loss: 52.428766
----
 sul'd legrur, herobbercepndite I buckwart virfame Stayy ih lut,
E's senourt a myoun febatpu't fiy lownden.
Yow nowe extreavestur willek avenseng ly noamcess, je shact;
This the suy, ard sthals
Thmibl? 
----
iter 72000, loss: 52.254165
----
 ousech?t for Kigh
Re; bo hadr 

----
 ing the kess to what ursish, thay ullse I hath lisply took:
I mat,
I, but to hou refaol me go my my buist my that dadem anid to I wiyd in fave shat pywirtiss bethar sivophor ty otens's laptir.
Gedbero 
----
iter 103000, loss: 52.615624
----
 ugy't blidnvy, the of cuwt fheremed Pome hato,
The't: and lord epldeseor.

GLOWIOHO:
I'ler mboules have thes onitnisp
yill ty his daa. Wau, lirenun weples it thakss wher ho he-halk it Ond all yithy!
T 
----
iter 104000, loss: 52.375006
----
 : his sheil clierld waglywent babus is if thou brictid.

LOCINGHI:
Youre grows.
Whast.
It buin thCor insfrage,
Hem, the pecut O and mree sheds, gratisess?

PEKE:
Willors
Nord it lell hit tneejrees:
Th 
----
iter 105000, loss: 52.150436
----
 ou quieg pus corth sabe or hough
It the,
And heay, in amre
I.

MEOLOG RICLARD IFRY:
Trimthis sham deare do his recly;
Dee o on aixt, whur of to wingey?
On thou opreesice brean:
Seam geay that nrea sou 
----
iter 106000, loss: 51.625186
----
 ot steram
lak
I browern ik

----
 ece, Withicl.

SIA:
O
GRIDULUS:
SakeBthmeinse theye so bece, but sinLurm'dned, sin:
Lit his meucfow clouss uaw hore;
In in the loveent ofice hive poweans daws criers she furgeas'd gou my caof
That sid 
----
iter 137000, loss: 51.194046
----
 I gau; on.

AScearawe moo: I, worde theils. and Casto! sible, the pery hare it
Tor favning amy Cilf her act'ly sore the stiue!

Fpwatvitizes, ass in praol he henver:
To
deryor?


DTENIUS:
Yord in I ha 
----
iter 138000, loss: 50.483787
----
 pe is a cnochmand. the ran vireand lopeans The eand:
The thy teans,
Orsioketame.

Fidf, polp a beslicisealn, hark. yould, per couund, did himgelarm cours
That it on proves,
I for thall bmy minw
Thtu t 
----
iter 139000, loss: 50.833001
----
 .
To sore them misind- it I with! haoke, do, by. Gom have mo wandillo: 'lle curcerele.

MENCRIUS:

MIO:
Thill ie it angher shand:,
At it ton'el chave a
KE kied. late I nops, puol o'd thav gout hare To 
----
iter 140000, loss: 51.351240
----
 uevel fane.

VIOF
MENTALIN

...

----
 cious than come.

DUKEh Enchiave be by to of I de.

HORTES:

CMORD IINA:
I tond a same!

HENUMEN
IFAlifful not thou arcing till freede pream
Andels alut of shal to distry? made, it smy detcelves, mere 
----
iter 21965000, loss: 44.880752
----
 m your se jays?

PROKE VOLINAURD:
Now and, why innost to thank, day ast of thing than sires
For me, me plade hit seity dot
It theeg
Nor palood allst, and fared dice cran in foot camm?
Will agaiant
Whe 
----
iter 21966000, loss: 44.853342
----
 hy, of my that Barreawnatooty: with I may, the tor love bomm your loves that hath morse my souch.

GRESPA:
My have by mus the ry us!
Nathy, Contred'd? Ge's breat who Cand him new bum
Ed as your quee,  
----
iter 21967000, loss: 44.980323
----
 es.
Your as aftemign somplest,
And bidrence lord
Could slen hourd naying repipul grookes,-'
What yet has! would
O, awo. lord have, af pain boven bonoul to wimse thonk telittines. Core to my virss of w 
----
iter 21968000, loss: 43.035200
----
 GICI:
Coll then mu

----
 anefres! it tell foe.

HISTEO:
Has duods pees; neet what a, beebre, tell fir
I fearinou A Sectilion, usts agklefst may quioke light him him the bederty cordy.
May not lord;
Grien as a fast shoures pay 
----
iter 21999000, loss: 43.798309
----
 :
He hearrens, dets wither: beignt.

BAMTONTE YES:
Think perst he the lan shemprepthign enate,
This did like to desblentest heep thid as here the telve dooss ashy sending thou means:
If about brasbize 
----
iter 22000000, loss: 44.207457
----
 nghe, look these to know.

KING RAMIS:
Sumossoldly.

CARIP ALUENUESO:
I both sut.

CICHIO:
What, I will Jupp hitheranet his rment pinks of here it your; ree any, samewter.

Sechany my saved;
And him,  
----
iter 22001000, loss: 44.407137
----
  I lord: rove ssore: gulrece you dill!

WIRIULE:
Love;
As than a are
In a
Fantel me neckead's she
'dy a frouse, I like exestioge more, hean have fires'd. I fist! I mold havice old to curut me,
In onal 
----
iter 22002000, loss: 43.976239
----
 po.

NII
HENRY BOL

----
 d ygseng: shore;
Have is
for know sist and thrivemped,
Ther?

BOP YORK:
That repuchenen; thy.

SICININIE:
Butched bourgal ray arthy you depity, thus nent tescows Is colood!

SABENCO RATIS:
Tean
Of sug 
----
iter 22033000, loss: 43.988395
----
 , that, fearescowle, groman.

So cants upseep to bemusies:
Mesemion:
That
I jeseypare
And duep a fiely herp his come drnodets
fer ala sweece; in that wooss, the bele, which till theireh! Woubjech on
D 
----
iter 22034000, loss: 43.766485
----
 ks,
Ot; I male but I cannos!

BIA:
There this eavant iffon the well
But I hease out hath to them from nate tryming is to forss.

KING EDWARD I Nus
Mewly when to not lord to Franpunruce is dewn: haste, 
----
iter 22035000, loss: 45.479729
----
 'd; that see: for of to high;
Brainnenable pally and Gondies.

Senxext, me send with her head
The spore, hears!
There her a sume 'lore swe resestens the podry.

PRUTERSOKN:
Well
Mand it Romarding dit  
----
iter 22036000, loss: 44.255702
----
 y saad, sting to m

----
 h streasio, Ribjeer's of tmobe; loved alast?
Man,
And Bane my remodrold he fayebl to take these war-fal, uponss your;
This, i, honds hadouns seed fof true I conge.

WARDITANAA:
What of whom leave
And  
----
iter 22067000, loss: 42.824264
----
 s will am I am of me capom.

Lorn on it, come feart of thou liover'st it a kelfforflen in's cour love; King Mannd thy not Letchers
Ind sesfuce
Thy bevive not.

ANTESSLI:
How warts of couser, I toling  
----
iter 22068000, loss: 42.739679
----
 Menjorsed no leing your peramlss, more of blecefceon; your his drentt marry the?
Neak not patten com;
Here casares in shing morls our then then; heret your taRo amem,
In bilk,
Herow;
Se a?

RICHMONSED 
----
iter 22069000, loss: 44.503088
----
  fie! prrook;
Lood fayer: his queightachers;
Me grace Kischallied of ander. Dim Marscuth telt; mynich mothlangetsecs the moalters but onne, Edward:
All
Hath thy not reverw's your to nemplor wie dead M 
----
iter 22070000, loss: 44.722368
----
 tare, oins I frans

KeyboardInterrupt: 